In [9]:
import requests
from haystack.document_stores.elasticsearch import ElasticsearchDocumentStore
from haystack.nodes import DensePassageRetriever
from transformers import pipeline
from haystack.nodes import QuestionGenerator
import PyPDF2
import pandas as pd
import re
import json
import pandas
import wikipedia
import nltk
from nltk.tokenize import sent_tokenize
import difflib
from transformers import BertForQuestionAnswering

In [2]:
wiki = wikipedia.summary('Philosophy_of_mind', sentences=15)
len(wiki)

1738

In [3]:
wikidata = sent_tokenize(wiki)

In [41]:
with open('filo.txt', 'w') as file:
    for i in wikidata:
        file.write(i + "\n")


In [4]:
# txt=x.extract_text(0)
txt=wiki
# text=open(r"/home/pancrackhead/Desktop/berikc_stable/pdf.txt")
qg = QuestionGenerator()
rfg = qg.generate(txt)

/home/pancrackhead/anaconda3/lib/python3.10/site-packages/torch/_utils.py:776: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
Using sep_token, but it is not set yet.


In [11]:
rfg[15]

'What is the ontological status of mental properties?'

In [5]:
requests.get('http://localhost:9200/_cluster/health').json()

doc_store = ElasticsearchDocumentStore(
    host='localhost',
    username='', password='',
    index='aurelius'
)

# data = data.split('\n')

data_json = [
    {
        'content': paragraph,
        'meta': {
            'source': 'filo'
        }
    } for paragraph in txt
]

doc_store.write_documents(data_json)
requests.get('http://localhost:9200/aurelius/_count').json()

/home/pancrackhead/anaconda3/lib/python3.10/site-packages/elasticsearch/connection/base.py:200: ElasticsearchWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.17/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchWarning)


{'count': 597,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0}}

In [6]:

retriever = DensePassageRetriever(
    document_store=doc_store,
    query_embedding_model='facebook/dpr-question_encoder-single-nq-base',
    passage_embedding_model='facebook/dpr-ctx_encoder-single-nq-base',
    use_gpu=True,
    embed_title=True
)

doc_store.update_embeddings(retriever=retriever)

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'DPRQuestionEncoderTokenizer'. 
The class this function is called from is 'DPRContextEncoderTokenizerFast'.


Updating embeddings:   0%|          | 0/597 [00:00<?, ? Docs/s]

Create embeddings:   0%|          | 0/608 [00:00<?, ? Docs/s]

In [46]:
# rfg[7]
for i in range(9):
    print(rfg[i])

What branch of philosophy studies the ontology and nature of the mind and its relationship with the body?
What is a paradigmatic issue in philosophy of mind?
The hard problem of consciousness and the nature of particular mental states are addressed by what?
Mental events, mental functions, mental properties, consciousness and its neural correlates, the ontology of the mind, cognition and of thought are studied by what researchers?
What are the two central schools of thought on the mind-body problem?
What does Dualism find its entry into Western philosophy?
Who introduced dualism to Western philosophy in the 17th century?
What do substance dualists believe the mind is?
Which type of dualist believes the mind to be a group of independent properties?


In [7]:
# question_answerer = pipeline("question-answering", model='distilbert-base-cased-distilled-squad')

# # prompt = rfg[7]
# prompt= "What is dualism??"
# answers = []
# prompts = []
# for i in range(len(rfg)):
#     prompt = rfg[i]
#     ans = []
#     score = []
#     con = retriever.retrieve(prompt)
#     for i in con:
#         x = i.content
#         result = question_answerer(question=prompt, context=context)
#         context = x
#         ans.append(result['answer'])
#         score.append(result['score'])
#     score, ans = zip(*sorted(zip(score, ans), reverse=True))

#     print(prompt)
#     print(score[0])
#     print(ans[0])
#     prompt = prompt
#     ans1= ans[0]
#     prompts.append(prompt)
#     answers.append(ans[0])



NameError: name 'context' is not defined

In [58]:
print(answers)

['formative', 'inquiry', 'The ruling principle', 'Thou', 'Reason and the reasoning art', 'Reason and the reasoning art', 'Epictetus', 'unity', 'ruling principle', 'The ruling principle', 'Epictetus', 'temperance', 'atoms', 'temperance', 'freedom from error and from deception', 'social']


In [57]:
with open('questions_gg.txt', 'w') as file:
    for i in prompts:
        file.write(i + "\n")

In [59]:
with open('answers_gg.txt', 'w') as file:
    for i in answers:
        file.write(i + "\n")

In [70]:

questions_file = "questions_gg.txt"
answers_file = "answers_gg.txt"
output_file = "squad_dataset_train.json"


with open(questions_file, "r") as q_file:
    questions = q_file.readlines()

with open(answers_file, "r") as a_file:
    answers = a_file.readlines()

dataset = {
    "version": "v2.0",
    "data": []
}

for q_text, a_text in zip(questions, answers):
    q_text = q_text.strip()
    a_text = a_text.strip()

    matcher = difflib.SequenceMatcher(None, a_text, q_text)
    match = matcher.find_longest_match(0, len(a_text), 0, len(q_text))
    answer_start = match.a
    qas = [
        {
            "question": q_text,
            "id": str(hash(q_text)),  
            "answers": [
                {
                    "text": a_text,
                    "answer_start": answer_start  
                }
            ],
            "is_impossible": False
        }
    ]

    context = a_text  

    dataset["data"].append({
        "title": "filozofia",
        "paragraphs": [
            {
                "qas": qas,
                "context": context
            }
        ]
    })


with open(output_file, "w") as out_file:
    json.dump(dataset, out_file, indent=2)

In [3]:
j = open('dev-v2.0.json', 'r')
data = json.load(j)
 
print(json.dumps(data, indent=1))


/tmp/ipykernel_7950/2437465490.py:1: ResourceWarning: unclosed file <_io.TextIOWrapper name='dev-v2.0.json' mode='r' encoding='UTF-8'>
  j = open('dev-v2.0.json', 'r')


{
 "version": "v2.0",
 "data": [
  {
   "title": "Normans",
   "paragraphs": [
    {
     "qas": [
      {
       "question": "In what country is Normandy located?",
       "id": "56ddde6b9a695914005b9628",
       "answers": [
        {
         "text": "France",
         "answer_start": 159
        },
        {
         "text": "France",
         "answer_start": 159
        },
        {
         "text": "France",
         "answer_start": 159
        },
        {
         "text": "France",
         "answer_start": 159
        }
       ],
       "is_impossible": false
      },
      {
       "question": "When were the Normans in Normandy?",
       "id": "56ddde6b9a695914005b9629",
       "answers": [
        {
         "text": "10th and 11th centuries",
         "answer_start": 94
        },
        {
         "text": "in the 10th and 11th centuries",
         "answer_start": 87
        },
        {
         "text": "10th and 11th centuries",
         "answer_start": 94
        },
     

In [ ]:
j = open('train-v2.0.json', 'r')
data = json.load(j)
 
print(json.dumps(data, indent=1))

In [2]:
j = open('updated_squad_dataset.json', 'r')
data = json.load(j)
 
print(json.dumps(data, indent=1))

{
 "version": "v2.0",
 "data": [
  {
   "title": "stolik",
   "paragraphs": [
    {
     "qas": [
      {
       "question": "From whom did I learn good morals and the government of my temper?",
       "id": 0,
       "answers": [
        {
         "text": "my grandfather Verus",
         "answer_start": 5
        }
       ],
       "is_impossible": false
      }
     ],
     "context": "From my grandfather Verus I learned good morals and the government of my temper."
    },
    {
     "qas": [
      {
       "question": "From my mother, piety and beneficence, and abstinence, not only from evil deeds, but even from evil thoughts?",
       "id": 1,
       "answers": [
        {
         "text": "not only from evil deeds, but even from evil thoughts",
         "answer_start": 55
        }
       ],
       "is_impossible": false
      },
      {
       "question": "What did my great-grandfather not frequent?",
       "id": 2,
       "answers": [
        {
         "text": "public schools